In [7]:
import sys
sys.path += ['../..']
sys.path += ['..']

from data_collection.data_collection import LoggerSet, Logger

import numpy as np
import pandas as pd
import plotly.express as px
from data_collection.video_data import get_frame_iterator
from pathlib import Path
from typing import Iterable, Tuple, List
from tqdm import tqdm
import datetime
import tensorflow as tf
import tensorflow.keras as keras

%load_ext autoreload
%autoreload 2


2024-07-10 05:39:51.571304: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-07-10 05:39:52.225517: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


# Note


- Angle difference is necessary (at least diff to the initial angle)
- it doesn't even train well because the inital angles are different for different runs

# Loading data 

In [8]:
from with_linear_acc_v2 import Session
sessions_v0 = Session.load_multiple_session('../data/v0',         
    camera_log_name = 'PicameraV2', 
    angular_speed_control_log_name='AngularSpeedControlV2'
)
sessions_v30Jun = Session.load_multiple_session('../data/v30Jun')


[mov,mp4,m4a,3gp,3g2,mj2 @ 0x5b6d8a30fb00] moov atom not found
[mov,mp4,m4a,3gp,3g2,mj2 @ 0x5b6d89e35a80] moov atom not found
[mov,mp4,m4a,3gp,3g2,mj2 @ 0x5b6d896ea100] moov atom not found


In [9]:
def match_time(t1_col, t2_col, t1_offset_ms=0, t2_offset_ms=0, sort_check=True):
    """
    return the indices of t1_col that match t2
    """
    if sort_check: 
        sortedt1 = np.sort(t1_col)
        sortedt2 = np.sort(t2_col)
        sortedt1 = sortedt1[~np.isnan(sortedt1)]
        sortedt2 = sortedt2[~np.isnan(sortedt2)]

        assert np.all(t1_col[~np.isnan(t1_col)] == sortedt1)
        assert np.all(t2_col[~np.isnan(t2_col)] == sortedt2)
    return np.searchsorted(t1_col+pd.to_timedelta(t1_offset_ms, unit='ms'), t2_col+pd.to_timedelta(t2_offset_ms, unit='ms'))

In [41]:
def mean_nominmax(x):
    return (x.sum()-x.max()-x.min())/(len(x)-2)

def data_prep(obj: Session):

    adf = obj.data['angular_speed_control_df']
    cdf = obj.data['camera_df']

    def add_angle_offset_columns():

                
        offset_list = [50, 100, 200, 400, 800]
        tidxs = [
            match_time(adf['time_AngularSpeedControl'], cdf['time'],  t2_offset_ms=_offset)
            for _offset in offset_list
        ]
        col_names: List = ['angle']
        omega_shifted = np.concatenate([
                adf[col_names].values[_tidx] 
                for _tidx in tidxs
            ], axis=1)

        column_names = [c+'_'+str(t) for t in offset_list for c in col_names]
        cdf[column_names] = omega_shifted
        obj.data['add_angle_offset_columns'] = column_names

        return column_names

    angle_col_names = add_angle_offset_columns()

    def add_sin_cos():
        as_rad = cdf[angle_col_names]/180*np.pi
        sin_col = [c+'_sin' for c in angle_col_names]
        cos_col = [c+'_cos' for c in angle_col_names]

        cdf[sin_col] = np.sin(as_rad)
        cdf[cos_col] = np.cos(as_rad)
        
        obj.data['add_sin_cos'] =   sin_col+ cos_col

    add_sin_cos()

    def add_speed_column():

        tidx = match_time(cdf['time'],  adf['time_AngularSpeedControl'])
        adf['frame_match'] = tidx
        mean_speed = adf.groupby('frame_match')['speed'].mean()

        # this is the mean speed after the end (acquisition) of the frame until the end of next frame
        cdf['mean_speed'] = mean_speed

    add_speed_column()

    

def sample_prep(obj: Session):
    frames, camera_df = obj.data['frames'], obj.data['camera_df']

    camera_df = camera_df.query('mean_speed>0')
    out = camera_df[obj.data['add_sin_cos']]
    
    frames = frames[out.index]

    obj.samples = frames, out.values
    


def stack_samples(objs: List[Session], sample_axis=0):
    samples_stacked = []
    for s in zip(*[o.samples for o in objs]):
        samples_stacked.append(np.concatenate(s, axis=sample_axis))
    return samples_stacked



In [42]:
[data_prep(s) for s in tqdm(sessions_v30Jun+sessions_v0)]; 
[sample_prep(s) for s in tqdm(sessions_v30Jun+sessions_v0)]; 

x, y = stack_samples(sessions_v30Jun)

from train_tools import validation_chunk_split
train_idx, val_idx = validation_chunk_split(len(x), val_split=0.2)
train_x, train_y = x[train_idx], y[train_idx]
val_x, val_y = x[val_idx], y[val_idx]


100%|██████████| 4/4 [00:00<00:00, 53.49it/s]


In [43]:
px.line(sessions_v30Jun[0].samples[1])

## Inspection only

In [8]:
df_vis = sessions[0].data['angular_speed_control_df']

In [52]:

def mean_nominmax(x):
    return (x.sum()-x.max()-x.min())/(len(x)-2)
asd0 = df_vis['angular_velocity'].rolling(100).apply(mean_nominmax)#.shift(-99)

asd = df_vis['angular_velocity'].rolling(50).apply(mean_nominmax).shift(-25)
asd1 = df_vis['angular_velocity'].rolling(3).apply(mean_nominmax).shift(-2)


px.line(y=[asd1, asd, asd0])

In [54]:
px.line(df_vis, y=['angular_velocity_smooth', 'angular_velocity'])

In [83]:
px.imshow(sessions[0].data['frames'][-1000])

# Model

In [44]:
def get_model(lr=.1, other_metrics=[]):
    tf.keras.backend.clear_session()
    image_shape = 64, 114, 3

    img_aug_preprocess_layers = [
        keras.layers.RandomTranslation(0.05, 0.05, fill_mode='reflect'),
        keras.layers.RandomRotation(0.02, fill_mode='reflect'),
        keras.layers.RandomZoom(0.05, fill_mode='reflect'),
        keras.layers.RandomContrast(0.3),
        keras.layers.RandomBrightness(factor=0.6, value_range=[0, 1])
    ]
    
    layers =  [
        keras.layers.Conv2D(16, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(32, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(64, 5, strides=2, activation='relu'),         
        keras.layers.Conv2D(64, (5, 3), activation='relu'), 
        keras.layers.Flatten(),
        keras.layers.Dropout(0.2),
        
        keras.layers.Dense(64, activation='relu'), 
        keras.layers.Dense(64, activation='relu'), 
        keras.layers.Dense(10, activation='tanh'), 
    ]
    
    model = keras.Sequential(
        [
            keras.layers.InputLayer(image_shape),
            keras.layers.Rescaling(1/255), 
            *img_aug_preprocess_layers,
            *layers, 
        ])


    optimiser = keras.optimizers.Adam(lr)
    model.compile(optimizer=optimiser, loss='Huber', metrics=['MAE']+other_metrics)

    return model 

model = get_model()
model.summary()

2024-07-10 05:51:01.983310: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-07-10 05:51:02.016815: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-07-10 05:51:02.017056: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ rescaling (Rescaling)           │ (None, 64, 114, 3)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_translation              │ (None, 64, 114, 3)     │             0 │
│ (RandomTranslation)             │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_rotation                 │ (None, 64, 114, 3)     │             0 │
│ (RandomRotation)                │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_zoom (RandomZoom)        │ (None, 64, 114, 3)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_contrast                 │ (None, 64, 114, 3)     │             0 │
│ (RandomContrast)                │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_brightness               │ (None, 64, 114, 3)     │             0 │
│ (RandomBrightness)              │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d (Conv2D)                 │ (None, 30, 55, 16)     │         1,216 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_1 (Conv2D)               │ (None, 13, 26, 32)     │        12,832 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_2 (Conv2D)               │ (None, 5, 11, 64)      │        51,264 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_3 (Conv2D)               │ (None, 1, 9, 64)       │        61,504 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten (Flatten)               │ (None, 576)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 576)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 64)             │        36,928 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 64)             │         4,160 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 10)             │           650 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 168,554 (658.41 KB)

 Trainable params: 168,554 (658.41 KB)

 Non-trainable params: 0 (0.00 B)

In [45]:
from train_tools import find_lr, tg_notify, use_tensorboard, end_epoch_notify

In [46]:
find_lr(get_model(), train_x, train_y)
#tensorboard --logdir ./logs --bind_all

Epoch 1/100


2024-07-10 05:51:10.708110: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:465] Loaded cuDNN version 8907


168/168 ━━━━━━━━━━━━━━━━━━━━ 4s 7ms/step - MAE: 0.6335 - loss: 0.2516 - learning_rate: 1.0000e-06
Epoch 2/100
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.6341 - loss: 0.2507 - learning_rate: 1.1220e-06
Epoch 3/100
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.6350 - loss: 0.2508 - learning_rate: 1.2589e-06
Epoch 4/100
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 6ms/step - MAE: 0.6346 - loss: 0.2502 - learning_rate: 1.4125e-06
Epoch 5/100
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.6334 - loss: 0.2501 - learning_rate: 1.5849e-06
Epoch 6/100
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.6342 - loss: 0.2500 - learning_rate: 1.7783e-06
Epoch 7/100
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.6316 - loss: 0.2499 - learning_rate: 1.9953e-06
Epoch 8/100
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.6317 - loss: 0.2498 - learning_rate: 2.2387e-06
Epoch 9/100
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 6ms/step - MAE: 0.6324 - loss: 0.2500 - learning_rate: 2.5119e-06
Epoch 10/100
168/168 ━

In [48]:
model = get_model(1e-4)
model.fit(
    train_x,
    train_y,
    epochs=1000, 
    validation_data = (val_x, val_y),
    callbacks=[
        tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10),
        use_tensorboard('training'), 
        end_epoch_notify()
        ] 
    )

  0%|          | 0/4 [05:20<?, ?it/s]


Epoch 1/1000
168/168 ━━━━━━━━━━━━━━━━━━━━ 3s 8ms/step - MAE: 0.6328 - loss: 0.2500 - val_MAE: 0.6312 - val_loss: 0.2513
Epoch 2/1000
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.6324 - loss: 0.2495 - val_MAE: 0.6284 - val_loss: 0.2489
Epoch 3/1000
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.6288 - loss: 0.2466 - val_MAE: 0.6108 - val_loss: 0.2363
Epoch 4/1000
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.5939 - loss: 0.2284 - val_MAE: 0.5795 - val_loss: 0.2204
Epoch 5/1000
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.5584 - loss: 0.2095 - val_MAE: 0.5547 - val_loss: 0.2071
Epoch 6/1000
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.5227 - loss: 0.1914 - val_MAE: 0.5314 - val_loss: 0.1949
Epoch 7/1000
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step - MAE: 0.4835 - loss: 0.1717 - val_MAE: 0.5250 - val_loss: 0.1927
Epoch 8/1000
168/168 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - MAE: 0.4765 - loss: 0.1683 - val_MAE: 0.5145 - val_loss: 0.1942
Epoch 9/1000
168/168 ━━━━━━━━━━━━━━━━━━━

In [ ]:
#frames_reindexed#, other_inputs_reindexed, outputs

# visualise the performance

In [62]:
def get_slicer_for_sin_cos(total:int):
    def slicer(*nths):
        return sum([[_nth, _nth+total] for _nth in nths], start=[])
    return slicer
slicer = get_slicer_for_sin_cos(5)


In [65]:

#train_frames, train_other, train_out
val_idxv = np.sort(val_idx)
train_idxv = np.sort(train_idx)

val_y_pred = model.predict(x[val_idxv], batch_size=64)
train_y_pred = model.predict(x[train_idxv], batch_size=64)


val_outv = y[val_idxv]
train_outv = y[train_idxv]



px.line(np.c_[train_outv[:, slicer(3,4)], train_y_pred[:, slicer(3,4)]], title='train')

14/14 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
84/84 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step


In [66]:
px.line(np.c_[val_outv[:,  slicer(3,4)], val_y_pred[:,  slicer(3,4)]], title='val_train')

In [72]:
#model.export('29Jun-export.keras')
model.save('model2-10Jul.keras')


In [71]:
x_val2, y_val2 = stack_samples(sessions_v0)

y_val2_pred = model.predict(x_val2, batch_size=64)


215/215 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step


In [75]:
px.line(np.c_[y_val2[:, slicer(0)], y_val2_pred[:, slicer(0)]], title='val2')